In [10]:
import bs4
import pandas as pd
import requests
import re

from urllib.parse import urljoin

## PPP source CSV discovery

In [3]:
ppp_base_url = 'https://data.sba.gov'
ppp_data_url = urljoin(ppp_base_url, 'dataset/ppp-foia')
page_content = requests.get(ppp_data_url).content
soup = bs4.BeautifulSoup(page_content, 'html.parser')
data_links = soup.find_all('a', attrs={'title': re.compile(r'\.csv$')})
csv_list = [{'url': urljoin(ppp_base_url, '/'.join([link.get('href'), 'download', link.get('title')])), 'filename': link.get('title')} for link in data_links]
csv_list

[{'url': 'https://data.sba.gov/dataset/ppp-foia/resource/c1275a03-c25c-488a-bd95-403c4b2fa036/download/public_150k_plus_240930.csv',
  'filename': 'public_150k_plus_240930.csv'},
 {'url': 'https://data.sba.gov/dataset/ppp-foia/resource/cff06664-1f75-4969-ab3d-6fa7d6b4c41e/download/public_up_to_150k_1_240930.csv',
  'filename': 'public_up_to_150k_1_240930.csv'},
 {'url': 'https://data.sba.gov/dataset/ppp-foia/resource/1e6b6629-a5aa-46e6-a442-6e67366d2362/download/public_up_to_150k_2_240930.csv',
  'filename': 'public_up_to_150k_2_240930.csv'},
 {'url': 'https://data.sba.gov/dataset/ppp-foia/resource/644c304a-f5ad-4cfa-b128-fe2cbcb7b26e/download/public_up_to_150k_3_240930.csv',
  'filename': 'public_up_to_150k_3_240930.csv'},
 {'url': 'https://data.sba.gov/dataset/ppp-foia/resource/98af633d-eb1b-4d4b-995d-330962e6c38d/download/public_up_to_150k_4_240930.csv',
  'filename': 'public_up_to_150k_4_240930.csv'},
 {'url': 'https://data.sba.gov/dataset/ppp-foia/resource/3b407e04-f269-47a0-a5fe-

In [4]:
import pandas as pd

first_csv = csv_list[0].get('url')
first_file = pd.read_csv(first_csv, encoding_errors='replace')
first_file.columns

KeyboardInterrupt: 

In [9]:
from io import StringIO
census_file = 'https://www2.census.gov/programs-surveys/popest/datasets/2010-2020/counties/asrh/CC-EST2020-ALLDATA.csv'
csv = requests.get(census_file, verify=False).text
pd.read_csv(StringIO(csv)).head()

/Users/Darren/miniconda3/envs/ppp_lending_analysis/lib/python3.11/site-packages/urllib3/connectionpool.py:1097: InsecureRequestWarning: Unverified HTTPS request is being made to host 'www2.census.gov'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(
/var/folders/b8/frpyqjx134d8nmnpx1t2ckvc0000gp/T/ipykernel_25435/3241858606.py:5: DtypeWarning: Columns (7,8,9,10,11,12,13,14,15,16,17,18,19,20,21,22,23,24,25,26,27,28,29,30,31,32,33,34,35,36,37,38,39,40,41,42,43,44,45,46,47,48,49,50,51,52,53,54,55,56,57,58,59,60,61,62,63,64,65,66,67,68,69,70,71,72,73,74,75,76,77,78,79) have mixed types. Specify dtype option on import or set low_memory=False.
  pd.read_csv(StringIO(csv)).head()


SUMLEV  STATE  COUNTY   STNAME         CTYNAME  YEAR  AGEGRP TOT_POP  \
0      50      1       1  Alabama  Autauga County     1       0   54571   
1      50      1       1  Alabama  Autauga County     1       1    3579   
2      50      1       1  Alabama  Autauga County     1       2    3991   
3      50      1       1  Alabama  Autauga County     1       3    4290   
4      50      1       1  Alabama  Autauga County     1       4    4290   

  TOT_MALE TOT_FEMALE  ... HWAC_MALE HWAC_FEMALE HBAC_MALE HBAC_FEMALE  \
0    26569      28002  ...       607         538        57          48   
1     1866       1713  ...        77          56         9           5   
2     2001       1990  ...        64          66         2           3   
3     2171       2119  ...        51          57        13           7   
4     2213       2077  ...        48          44         7           5   

  HIAC_MALE HIAC_FEMALE HAAC_MALE HAAC_FEMALE HNAC_MALE HNAC_FEMALE  
0        26          32         9          11        19          10  
1         4           1         0           0         2           1  
2         2           7         2           3         2           0  
3         5           5         2           1         1           1  
4         0           2         2           1         3           1  

[5 rows x 80 columns]

In [11]:
from pathlib import Path
Path(census_file).name

'CC-EST2020-ALLDATA.csv'

In [17]:
xwalk_path = 'https://www2.census.gov/geo/docs/reference/state.txt'
resp = requests.get(xwalk_path, verify=False)
pd.read_csv(StringIO(resp.text), sep='|').head()

/Users/Darren/miniconda3/envs/ppp_lending_analysis/lib/python3.11/site-packages/urllib3/connectionpool.py:1097: InsecureRequestWarning: Unverified HTTPS request is being made to host 'www2.census.gov'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(


STATE STUSAB  STATE_NAME  STATENS
0      1     AL     Alabama  1779775
1      2     AK      Alaska  1785533
2      4     AZ     Arizona  1779777
3      5     AR    Arkansas    68085
4      6     CA  California  1779778

## Cleaning result

Cleans state and county mismatches with regex reconciliation. Can be built into dbt view for reconciliation. Or use in a bridge table for exact matching across sources. Only results below are mismatches, which do not have any county-level correlation. 



In [26]:
import duckdb

db_path = '../data/ppp_loan_analysis.duckdb'

query = """
	SELECT
		s.state_name,
		p.project_state,
		p.project_county_name,
		c.ctyname,
		COUNT(p.*) AS ppp_records
	FROM
		bronze.paycheck_protection_loans p
	LEFT JOIN bronze.state_crosswalk s 
	ON
		p.project_state = s.stusab
	LEFT JOIN bronze.census_2020_estimates c 
	ON
		s.state_name = c.stname
			AND LOWER(
					REGEXP_REPLACE(
						REGEXP_REPLACE(
							CASE 
								WHEN p.project_state = 'VA'
								AND p.project_county_name IN ('BRISTOL', 'RADFORD', 'EMPORIA', 'SALEM')
									THEN p.project_county_name || ' city'
								WHEN p.project_state = 'SD'
								AND p.project_county_name = 'PINE RIDGE'
									THEN 'OGLALA LAKOTA'
								WHEN p.project_county_name = 'DONA ANA'
									THEN 'Doña Ana'
								ELSE p.project_county_name
							END,
							'^(ST |SAINTE)', 'SAINT', 'i'),
					'[ -]|''', '', 'g')
				) =
			LOWER(
				REGEXP_REPLACE(
					REGEXP_REPLACE(
						REGEXP_REPLACE(c.ctyname, ' (County|Parish|City and Borough|Borough|Municipality|Census Area)', '', 'i'), 
					'(St\. |Ste\. |^St )', 'SAINT', 'i'),
				'[ -]|''', '', 'g')
			)
	WHERE
		c.ctyname IS NULL
		AND p.project_county_name IS NOT NULL
		AND p.project_state NOT IN ('PR', 'MP', 'AE', 'VI', 'AS', 'GU')
	GROUP BY ALL
	ORDER BY
		p.project_state
"""

total_query = """
	SELECT COUNT(*) AS TOTAL
	FROM bronze.paycheck_protection_loans
"""

with duckdb.connect(db_path) as conn:
    df = conn.sql(query).df()
    total = conn.sql(total_query).fetchone()[0]
    
print(f"Total of {df['ppp_records'].sum()} without property county, out of {total}, or {df['ppp_records'].sum()/total:.4%} of all records.")  

Total of 1562 without property county, out of 11468210, or 0.0136%


## Election result discovery

In [5]:
url = 'https://dataverse.harvard.edu/api/access/datafile/11739050?format=original&gbrecs=true'
resp = requests.get(url).content

b"year,state,state_po,county_name,county_fips,office,candidate,party,candidatevotes,totalvotes,version,mode\r\n2000,ALABAMA,AL,AUTAUGA,01001,US PRESIDENT,AL GORE,DEMOCRAT,4942,17208,20250712,TOTAL\r\n2000,ALABAMA,AL,AUTAUGA,01001,US PRESIDENT,GEORGE W. BUSH,REPUBLICAN,11993,17208,20250712,TOTAL\r\n2000,ALABAMA,AL,AUTAUGA,01001,US PRESIDENT,OTHER,OTHER,113,17208,20250712,TOTAL\r\n2000,ALABAMA,AL,AUTAUGA,01001,US PRESIDENT,RALPH NADER,GREEN,160,17208,20250712,TOTAL\r\n2000,ALABAMA,AL,BALDWIN,01003,US PRESIDENT,AL GORE,DEMOCRAT,13997,56480,20250712,TOTAL\r\n2000,ALABAMA,AL,BALDWIN,01003,US PRESIDENT,GEORGE W. BUSH,REPUBLICAN,40872,56480,20250712,TOTAL\r\n2000,ALABAMA,AL,BALDWIN,01003,US PRESIDENT,OTHER,OTHER,578,56480,20250712,TOTAL\r\n2000,ALABAMA,AL,BALDWIN,01003,US PRESIDENT,RALPH NADER,GREEN,1033,56480,20250712,TOTAL\r\n2000,ALABAMA,AL,BARBOUR,01005,US PRESIDENT,AL GORE,DEMOCRAT,5188,10395,20250712,TOTAL\r\n2000,ALABAMA,AL,BARBOUR,01005,US PRESIDENT,GEORGE W. BUSH,REPUBLICAN,5096,1039

## QCEW data discovery

Retrieve codes for areas and then iterate through to get industry detail for each area.


In [8]:
area_url = 'https://data.bls.gov/cew/doc/titles/area/area_titles.csv'
df = pd.read_csv(area_url).head(10)
df

area_fips                                      area_title
0     US000                                      U.S. TOTAL
1     USCMS      U.S. Combined Statistical Areas (combined)
2     USMSA  U.S. Metropolitan Statistical Areas (combined)
3     USNMS   U.S. Nonmetropolitan Area Counties (combined)
4     01000                            Alabama -- Statewide
5     01001                         Autauga County, Alabama
6     01003                         Baldwin County, Alabama
7     01005                         Barbour County, Alabama
8     01007                            Bibb County, Alabama
9     01009                          Blount County, Alabama

In [25]:
area_path = f'http://data.bls.gov/cew/data/api/2019/a/area/10001.csv'
df = pd.read_csv(area_path)

In [26]:
import duckdb

duckdb.sql("""
    SELECT *
    FROM df
    WHERE (agglvl_code = 74 OR industry_code = '10')
    AND own_code = 5
""").df()

area_fips  own_code industry_code  agglvl_code  size_code  year qtr  \
0       10001         5            10           71          0  2019   A   
1       10001         5            11           74          0  2019   A   
2       10001         5            21           74          0  2019   A   
3       10001         5            22           74          0  2019   A   
4       10001         5            23           74          0  2019   A   
5       10001         5         31-33           74          0  2019   A   
6       10001         5            42           74          0  2019   A   
7       10001         5         44-45           74          0  2019   A   
8       10001         5         48-49           74          0  2019   A   
9       10001         5            51           74          0  2019   A   
10      10001         5            52           74          0  2019   A   
11      10001         5            53           74          0  2019   A   
12      10001         5            54           74          0  2019   A   
13      10001         5            55           74          0  2019   A   
14      10001         5            56           74          0  2019   A   
15      10001         5            61           74          0  2019   A   
16      10001         5            62           74          0  2019   A   
17      10001         5            71           74          0  2019   A   
18      10001         5            72           74          0  2019   A   
19      10001         5            81           74          0  2019   A   

   disclosure_code  annual_avg_estabs  annual_avg_emplvl  ...  \
0                N               4226                  0  ...   
1                N                 41                  0  ...   
2                N                  3                  0  ...   
3             None                 10                304  ...   
4             None                421               2687  ...   
5             None                 62               4892  ...   
6             None                207               1108  ...   
7             None                529               9256  ...   
8             None                128               2524  ...   
9             None                 48                403  ...   
10            None                211               1546  ...   
11            None                136                405  ...   
12            None                495               1830  ...   
13            None                 16                330  ...   
14            None                330               2604  ...   
15            None                 39                443  ...   
16            None                880              10424  ...   
17            None                 68               1552  ...   
18            None                292               6671  ...   
19            None                313               1647  ...   

    oty_total_annual_wages_chg  oty_total_annual_wages_pct_chg  \
0                            0                             0.0   
1                            0                             0.0   
2                            0                             0.0   
3                     -2578291                            -8.1   
4                     17683317                            13.2   
5                            0                             0.0   
6                      3242638                             5.4   
7                      4144155                             1.5   
8                      7507236                             7.5   
9                      6642276                            39.9   
10                    26803586                            27.8   
11                     -450020                            -2.8   
12                           0                             0.0   
13                           0                             0.0   
14                     9001221                             9.2   
15    

In [33]:
area_titles = 'https://data.bls.gov/cew/doc/titles/area/area_titles.csv'

duckdb.sql(f"""
    SELECT *
    FROM read_csv_auto('{area_titles}')
""").to_nu


{'area_fips': array(['US000', 'USCMS', 'USMSA', ..., 'USCMS', 'USMSA', 'USNMS'],
       shape=(9458,), dtype=object),
 'area_title': array(['U.S. TOTAL', 'U.S. Combined Statistical Areas (combined)',
        'U.S. Metropolitan Statistical Areas (combined)', ...,
        'U.S. Combined Statistical Areas (combined)',
        'U.S. Metropolitan Statistical Areas (combined)',
        'U.S. Nonmetropolitan Area Counties (combined)'],
       shape=(9458,), dtype=object)}

In [20]:
import requests
from dlt.sources.rest_api import rest_api_source, RESTClient

# Create session with SSL verification disabled
session = requests.Session()
session.verify = False

# Create client with SSL verification disabled
client = RESTClient('https://www2.census.gov/geo/docs/reference/', session=session)
client.get('state.txt').text[0:100]

/Users/Darren/miniconda3/envs/ppp_lending_analysis/lib/python3.11/site-packages/urllib3/connectionpool.py:1097: InsecureRequestWarning: Unverified HTTPS request is being made to host 'www2.census.gov'. Adding certificate verification is strongly advised. See: https://urllib3.readthedocs.io/en/latest/advanced-usage.html#tls-warnings
  warnings.warn(


'STATE|STUSAB|STATE_NAME|STATENS\n01|AL|Alabama|01779775\n02|AK|Alaska|01785533\n04|AZ|Arizona|01779777\n'

## Inspect QCEW bulk CSV file

In [64]:
import zipfile
import io
import requests

url = 'https://data.bls.gov/cew/data/files/2020/csv/2020_annual_by_area.zip'

zip_download = requests.get(url)

In [71]:
import duckdb
import re
from pathlib import Path
with zipfile.ZipFile(io.BytesIO(zip_download.content), 'r') as zf:
    zip_paths = [
        file for file in zf.namelist()[1:]
        if re.search(r'\d{5}', Path(file).name)
    ]
    zip_path_sample = zip_paths[0:5]
    for zip_path in zip_path_sample:
        file_bytes = io.BytesIO(zf.read(zip_path))
        print(pd.read_csv(file_bytes).head())

   area_fips  own_code industry_code  agglvl_code  size_code  year qtr  \
0       1000         0            10           50          0  2020   A   
1       1000         1            10           51          0  2020   A   
2       1000         1           102           52          0  2020   A   
3       1000         1          1021           53          0  2020   A   
4       1000         1          1022           53          0  2020   A   

  disclosure_code            area_title           own_title  ...  \
0             NaN  Alabama -- Statewide       Total Covered  ...   
1             NaN  Alabama -- Statewide  Federal Government  ...   
2             NaN  Alabama -- Statewide  Federal Government  ...   
3             NaN  Alabama -- Statewide  Federal Government  ...   
4             NaN  Alabama -- Statewide  Federal Government  ...   

  oty_total_annual_wages_chg oty_total_annual_wages_pct_chg  \
0                 2507023243                            2.6   
1                  2